# Capstone Project - The Battle of the Neighborhoods - New York City

## Table of contents
* [Introduction: Business Problem](#introduction)
* [Data](#data)
* [Methodology](#methodology)
* [Analysis](#analysis)
* [Results and Discussion](#results)
* [Conclusion](#conclusion)
* [Future Work](#futurework)



## Introduction: Business Problem <a name="introduction"></a>

In this project we will try to find an optimal location for a restaurant. Specifically, this report will be targeted to stakeholders interested in opening an **Italian restaurant** in **New York City**, USA.

Since there are lots of restaurants in New York City we will try to detect **locations that are not already crowded with restaurants**. We are also particularly interested in **areas with no Italian restaurants in vicinity**. We would also prefer locations **as close to city center as possible**, assuming that first two conditions are met.

We will use our data science powers to generate a few most promissing neighborhoods based on this criteria. Advantages of each area will then be clearly expressed so that best possible final location can be chosen by stakeholders.

## Data <a name="data"></a>

Based on definition of our problem, factors that will influence our decission are:
* number of existing restaurants in the neighborhood (any type of restaurant)
* number of and distance to Italian restaurants in the neighborhood, if any
* distance of neighborhood from city center

We decided to use regularly spaced grid of locations, centered around city center, to define our neighborhoods.

Following data sources will be needed to extract/generate the required information:
* centers of candidate areas will be generated algorithmically and approximate addresses of centers of those areas will be obtained using **Google Maps API reverse geocoding**
* number of restaurants and their type and location in every neighborhood will be obtained using **Foursquare API**
* coordinate of New York City center will be obtained using **Google Maps API geocoding** 

### Neighborhood Candidates

Let's create latitude & longitude coordinates for centroids of our candidate neighborhoods. We will create a grid of cells covering our area of interest which is aprox. 12x12 killometers centered around New York City center.

Let's first find the latitude & longitude of New York city center, using specific, well known address and Google Maps geocoding API.

In [61]:
import requests

def get_coordinates(api_key, address, verbose=False):
    try:
        url = 'https://maps.googleapis.com/maps/api/geocode/json?key={}&address={}'.format(api_key, address)
        response = requests.get(url).json()
        if verbose:
            print('Google Maps API JSON result =>', response)
        results = response['results']
        geographical_data = results[0]['geometry']['location'] # get geographical coordinates
        lat = geographical_data['lat']
        lon = geographical_data['lng']
        return [lat, lon]
    except:
        return [None, None]

In [62]:
google_api_key = '..........'   
address = 'New York City, NY'
new_york_city_center = get_coordinates(google_api_key, address)
print('Coordinate of {}: {}'.format(address, new_york_city_center))

Coordinate of New York City, NY: [40.7127753, -74.0059728]


Now let's create a grid of area candidates, equaly spaced, centered around city center and within ~6km from it. Our neighborhoods will be defined as circular areas with a radius of 300 meters, so our neighborhood centers will be 600 meters apart.

To accurately calculate distances we need to create our grid of locations in Cartesian 2D coordinate system which allows us to calculate distances in meters (not in latitude/longitude degrees). Then we'll project those coordinates back to latitude/longitude degrees to be shown on Folium map. So let's create functions to convert between WGS84 spherical coordinate system (latitude/longitude degrees) and UTM Cartesian coordinate system (X/Y coordinates in  meters).

In [63]:
!pip install shapely
import shapely.geometry

!pip install pyproj
import pyproj

import math

def lonlat_to_xy(lon, lat):
    proj_latlon = pyproj.Proj(proj='latlong',datum='WGS84')
    proj_xy = pyproj.Proj(proj="utm", zone=33, datum='WGS84')
    xy = pyproj.transform(proj_latlon, proj_xy, lon, lat)
    return xy[0], xy[1]

def xy_to_lonlat(x, y):
    proj_latlon = pyproj.Proj(proj='latlong',datum='WGS84')
    proj_xy = pyproj.Proj(proj="utm", zone=33, datum='WGS84')
    lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
    return lonlat[0], lonlat[1]

def calc_xy_distance(x1, y1, x2, y2):
    dx = x2 - x1
    dy = y2 - y1
    return math.sqrt(dx*dx + dy*dy)

print('Coordinate transformation check')
print('-------------------------------')
print('new york city center longitude={}, latitude={}'.format(new_york_city_center[1], new_york_city_center[0]))
x, y = lonlat_to_xy(new_york_city_center[1], new_york_city_center[0])
print('new york city center UTM X={}, Y={}'.format(x, y))
lo, la = xy_to_lonlat(x, y)
print('new york city center longitude={}, latitude={}'.format(lo, la))


Coordinate transformation check
-------------------------------
new york city center longitude=-74.0059728, latitude=40.7127753
new york city center UTM X=-5822282.486116526, Y=9869599.497969413
new york city center longitude=-74.00597279999963, latitude=40.71277529999885


/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:12: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1


Let's create a **hexagonal grid of cells**: we offset every other row, and adjust vertical row spacing so that **every cell center is equally distant from all it's neighbors**.

In [64]:
new_york_city_center_x, new_york_city_center_y = lonlat_to_xy(new_york_city_center[1], new_york_city_center[0]) # City center in Cartesian coordinates

k = math.sqrt(3) / 2 # Vertical offset for hexagonal grid cells
x_min = new_york_city_center_x - 6000
x_step = 600
y_min = new_york_city_center_y - 6000 - (int(21/k)*k*600 - 12000)/2
y_step = 600 * k 

latitudes = []
longitudes = []
distances_from_center = []
xs = []
ys = []
for i in range(0, int(21/k)):
    y = y_min + i * y_step
    x_offset = 300 if i%2==0 else 0
    for j in range(0, 21):
        x = x_min + j * x_step + x_offset
        distance_from_center = calc_xy_distance(new_york_city_center_x, new_york_city_center_y, x, y)
        if (distance_from_center <= 6001):
            lon, lat = xy_to_lonlat(x, y)
            latitudes.append(lat)
            longitudes.append(lon)
            distances_from_center.append(distance_from_center)
            xs.append(x)
            ys.append(y)

print(len(latitudes), 'candidate neighborhood centers generated.')


/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:12: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:18: DeprecationWarning: This function

/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:18: DeprecationWarning: This function

/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:18: DeprecationWarning: This function

364 candidate neighborhood centers generated.


/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:18: DeprecationWarning: This function

Let's visualize the data we have so far: city center location and candidate neighborhood centers:

In [65]:
!pip install folium

import folium

In [66]:
map_new_york = folium.Map(location=new_york_city_center, zoom_start=13)
folium.Marker(new_york_city_center, popup='new york city center').add_to(map_new_york)
for lat, lon in zip(latitudes, longitudes):
    #folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_berlin) 
    folium.Circle([lat, lon], radius=195, color='blue', fill=False).add_to(map_new_york)
    #folium.Marker([lat, lon]).add_to(map_berlin)
map_new_york

OK, we now have the coordinates of centers of neighborhoods/areas to be evaluated, equally spaced (distance from every point to it's neighbors is exactly the same) and within ~6km from city center. 

Let's now use Google Maps API to get approximate addresses of those locations.

In [67]:
def get_address(api_key, latitude, longitude, verbose=False):
    try:
        url = 'https://maps.googleapis.com/maps/api/geocode/json?key={}&latlng={},{}'.format(api_key, latitude, longitude)
        response = requests.get(url).json()
        if verbose:
            print('Google Maps API JSON result =>', response)
        results = response['results']
        address = results[0]['formatted_address']
        return address
    except:
        return None

addr = get_address(google_api_key, new_york_city_center[0], new_york_city_center[1])
print('Reverse geocoding check')
print('-----------------------')
print('Address of [{}, {}] is: {}'.format(new_york_city_center[0], new_york_city_center[1], addr))

Reverse geocoding check
-----------------------
Address of [40.7127753, -74.0059728] is: 240 Broadway, New York, NY 10007, USA


In [68]:
print('Obtaining location addresses: ', end='')
addresses = []
for lat, lon in zip(latitudes, longitudes):
    address = get_address(google_api_key, lat, lon)
    if address is None:
        address = 'NO ADDRESS'
    address = address.replace(', USA', '') # We don't need country part of address
    addresses.append(address)
    print(' .', end='')
print(' done.')


Obtaining location addresses:  . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . done.


In [69]:
addresses[150:170]

['124 W 16th St, New York, NY 10011',
 '178 7th Ave, New York, NY 10011',
 '264 W 25th St, New York, NY 10001',
 '81 Rapelye St, Brooklyn, NY 11231',
 '225 Columbia St, Brooklyn, NY 11231',
 '123 Van Brunt St, Brooklyn, NY 11231',
 '2 Atlantic Ave, Brooklyn, NY 11201',
 'Pier 5 Brooklyn Bridge Park, Brooklyn, NY 11201',
 'Unnamed Road, Brooklyn Heights, NY 11201',
 'Unnamed Road, New York, NY 10038',
 '89 South St, New York, NY 10038',
 '221 Front St, New York, NY 10038',
 '122 Park Row, New York, NY 10007',
 'Collect Pond Park, 130 Leonard St, New York, NY 10013',
 '425 Broadway, New York, NY 10013',
 '66 Wooster St, New York, NY 10012',
 '139 Thompson St, New York, NY 10012',
 '24 Minetta Ln, New York, NY 10012',
 '33 Stonewall Pl, New York, NY 10014',
 '20 7th Ave, New York, NY 10011']

Looking good. Let's now place all this into a Pandas dataframe.

In [70]:
import pandas as pd

df_locations = pd.DataFrame({'Address': addresses,
                             'Latitude': latitudes,
                             'Longitude': longitudes,
                             'X': xs,
                             'Y': ys,
                             'Distance from center': distances_from_center})

df_locations.head(10)

Address   Latitude  Longitude             X  \
0   1626 Hooper St, Brooklyn, NY 11211  40.701263 -73.962112 -5.824082e+06   
1  556 Bedford Ave, Brooklyn, NY 11249  40.704797 -73.961984 -5.823482e+06   
2     172 S 9th St, Brooklyn, NY 11211  40.708330 -73.961856 -5.822882e+06   
3     158 S 3rd St, Brooklyn, NY 11211  40.711864 -73.961727 -5.822282e+06   
4     129 N 1st St, Brooklyn, NY 11249  40.715399 -73.961599 -5.821682e+06   
5      76 N 6th St, Brooklyn, NY 11249  40.718933 -73.961470 -5.821082e+06   
6    10 Nassau Ave, Brooklyn, NY 11222  40.722468 -73.961342 -5.820482e+06   
7     299 Park Ave, Brooklyn, NY 10017  40.696048 -73.966325 -5.824982e+06   
8  22 Flushing Ave, Brooklyn, NY 11205  40.699581 -73.966197 -5.824382e+06   
9     595 Kent Ave, Brooklyn, NY 11249  40.703114 -73.966069 -5.823782e+06   

              Y  Distance from center  
0  9.863884e+06           5992.495307  
1  9.863884e+06           5840.376700  
2  9.863884e+06           5747.173218  
3  9.863884e+06           5715.767665  
4  9.863884e+06           5747.173218  
5  9.863884e+06           5840.376700  
6  9.863884e+06           5992.495307  
7  9.864403e+06           5855.766389  
8  9.864403e+06           5604.462508  
9  9.864403e+06           5408.326913

...and let's now save/persist this data into local file.

In [71]:
df_locations.to_pickle('./locations.pkl')    

### Foursquare
Now that we have our location candidates, let's use Foursquare API to get info on restaurants in each neighborhood.

We're interested in venues in 'food' category, but only those that are proper restaurants - coffee shops, pizza places, bakeries etc. are not direct competitors so we don't care about those. So we will include in out list only venues that have 'restaurant' in category name, and we'll make sure to detect and include all the subcategories of specific 'Italian restaurant' category, as we need info on Italian restaurants in the neighborhood.

Foursquare credentials are defined in hidden cell bellow.

In [72]:
foursquare_client_id = '.........'
foursquare_client_secret = '..........'

In [73]:
# Category IDs corresponding to Italian restaurants were taken from Foursquare web site (https://developer.foursquare.com/docs/resources/categories):

food_category = '4d4b7105d754a06374d81259' # 'Root' category for all food-related venues

italian_restaurant_categories = ['4bf58dd8d48988d110941735','55a5a1ebe4b013909087cbb6','55a5a1ebe4b013909087cb7c',
                                 '55a5a1ebe4b013909087cba7','55a5a1ebe4b013909087cba1','55a5a1ebe4b013909087cba4',
                                 '55a5a1ebe4b013909087cb95','55a5a1ebe4b013909087cb89','55a5a1ebe4b013909087cb9b',
                                 '55a5a1ebe4b013909087cb98','55a5a1ebe4b013909087cbbf','55a5a1ebe4b013909087cb79',
                                 '55a5a1ebe4b013909087cbb0','55a5a1ebe4b013909087cbb3','55a5a1ebe4b013909087cb74',
                                 '55a5a1ebe4b013909087cbaa','55a5a1ebe4b013909087cb83','55a5a1ebe4b013909087cb8c',
                                 '55a5a1ebe4b013909087cb92','55a5a1ebe4b013909087cb8f','55a5a1ebe4b013909087cb86',
                                 '55a5a1ebe4b013909087cbb9','55a5a1ebe4b013909087cb7f','55a5a1ebe4b013909087cbbc',
                                 '55a5a1ebe4b013909087cb9e','55a5a1ebe4b013909087cbc2','55a5a1ebe4b013909087cbad']

def is_restaurant(categories, specific_filter=None):
    restaurant_words = ['restaurant', 'diner', 'taverna', 'steakhouse']
    restaurant = False
    specific = False
    for c in categories:
        category_name = c[0].lower()
        category_id = c[1]
        for r in restaurant_words:
            if r in category_name:
                restaurant = True
        if 'fast food' in category_name:
            restaurant = False
        if not(specific_filter is None) and (category_id in specific_filter):
            specific = True
            restaurant = True
    return restaurant, specific

def get_categories(categories):
    return [(cat['name'], cat['id']) for cat in categories]

def format_address(location):
    address = ', '.join(location['formattedAddress'])
    address = address.replace(', Deutschland', '')
    address = address.replace(', Germany', '')
    return address

def get_venues_near_location(lat, lon, category, client_id, client_secret, radius=500, limit=100):
    version = '20180724'
    url = 'https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&v={}&ll={},{}&categoryId={}&radius={}&limit={}'.format(
        client_id, client_secret, version, lat, lon, category, radius, limit)
    try:
        results = requests.get(url).json()['response']['groups'][0]['items']
        venues = [(item['venue']['id'],
                   item['venue']['name'],
                   get_categories(item['venue']['categories']),
                   (item['venue']['location']['lat'], item['venue']['location']['lng']),
                   format_address(item['venue']['location']),
                   item['venue']['location']['distance']) for item in results]        
    except:
        venues = []
    return venues


In [74]:
# Let's now go over our neighborhood locations and get nearby restaurants; we'll also maintain a dictionary of all found restaurants and all found italian restaurants

import pickle

def get_restaurants(lats, lons):
    restaurants = {}
    italian_restaurants = {}
    location_restaurants = []

    print('Obtaining venues around candidate locations:', end='')
    for lat, lon in zip(lats, lons):
        # Using radius=350 to meke sure we have overlaps/full coverage so we don't miss any restaurant (we're using dictionaries to remove any duplicates resulting from area overlaps)
        venues = get_venues_near_location(lat, lon, food_category, foursquare_client_id, foursquare_client_secret, radius=350, limit=100)
        area_restaurants = []
        for venue in venues:
            venue_id = venue[0]
            venue_name = venue[1]
            venue_categories = venue[2]
            venue_latlon = venue[3]
            venue_address = venue[4]
            venue_distance = venue[5]
            is_res, is_italian = is_restaurant(venue_categories, specific_filter=italian_restaurant_categories)
            if is_res:
                x, y = lonlat_to_xy(venue_latlon[1], venue_latlon[0])
                restaurant = (venue_id, venue_name, venue_latlon[0], venue_latlon[1], venue_address, venue_distance, is_italian, x, y)
                if venue_distance<=300:
                    area_restaurants.append(restaurant)
                restaurants[venue_id] = restaurant
                if is_italian:
                    italian_restaurants[venue_id] = restaurant
        location_restaurants.append(area_restaurants)
        print(' .', end='')
    print(' done.')
    return restaurants, italian_restaurants, location_restaurants

# Try to load from local file system in case we did this before
restaurants = {}
italian_restaurants = {}
location_restaurants = []
loaded = False
try:
    with open('restaurants_350.pkl', 'rb') as f:
        restaurants = pickle.load(f)
    with open('italian_restaurants_350.pkl', 'rb') as f:
        italian_restaurants = pickle.load(f)
    with open('location_restaurants_350.pkl', 'rb') as f:
        location_restaurants = pickle.load(f)
    print('Restaurant data loaded.')
    loaded = True
except:
    pass

# If load failed use the Foursquare API to get the data
if not loaded:
    restaurants, italian_restaurants, location_restaurants = get_restaurants(latitudes, longitudes)
    
    # Let's persists this in local file system
    with open('restaurants_350.pkl', 'wb') as f:
        pickle.dump(restaurants, f)
    with open('italian_restaurants_350.pkl', 'wb') as f:
        pickle.dump(italian_restaurants, f)
    with open('location_restaurants_350.pkl', 'wb') as f:
        pickle.dump(location_restaurants, f)
 

Restaurant data loaded.


In [75]:
import numpy as np

print('Total number of restaurants:', len(restaurants))
print('Total number of Italian restaurants:', len(italian_restaurants))
print('Percentage of Italian restaurants: {:.2f}%'.format(len(italian_restaurants) / len(restaurants) * 100))
print('Average number of restaurants in neighborhood:', np.array([len(r) for r in location_restaurants]).mean())


Total number of restaurants: 1935
Total number of Italian restaurants: 255
Percentage of Italian restaurants: 13.18%
Average number of restaurants in neighborhood: 9.10989010989011


In [76]:
print('List of all restaurants')
print('-----------------------')
for r in list(restaurants.values())[:10]:
    print(r)
print('...')
print('Total:', len(restaurants))

List of all restaurants
-----------------------
('5d4db7a190986c00088de8b0', 'אולם פרענקל ~ Elum Frankl (Elum Frankl)', 40.700458000000005, -73.960581, '762 Wythe Ave, Brooklyn, NY 11249, United States', 157, False, -5824213.63978717, 9863682.20109519)
('45f91993f964a52041441fe3', "Gottlieb's Restaurant", 40.70764197787768, -73.96123691979123, '352 Roebling St (Division Ave), Brooklyn, NY 11211, United States', 92, False, -5822997.08328189, 9863800.620478693)
('4becae892cf820a1991fb91c', 'Grill On Lee', 40.704392999999996, -73.958905, '108 Lee Ave, Brooklyn, NY 11211, United States', 263, False, -5823539.975809362, 9863484.274812369)
('3fd66200f964a5209beb1ee3', 'Peter Luger Steak House', 40.70995790682886, -73.96229110893742, '178 Broadway (at Driggs Ave), Brooklyn, NY 11211, United States', 298, False, -5822607.940229336, 9863947.578694936)
('53a1a98c498e019a787752d7', 'Meadowsweet', 40.71035245392043, -73.96326363144188, '149 Broadway (at Bedford Ave), Brooklyn, NY 11211, United Sta

In [77]:
print('List of Italian restaurants')
print('---------------------------')
for r in list(italian_restaurants.values())[:10]:
    print(r)
print('...')
print('Total:', len(italian_restaurants))

List of Italian restaurants
---------------------------
('4106ec80f964a520890b1fe3', 'Aurora', 40.715767452905396, -73.96464546639929, '70 Grand St (btwn Kent & Wythe Ave), Brooklyn, NY 11249, United States', 182, True, -5821630.794951575, 9864278.682805602)
('4f825769e4b024a26f122b5d', 'D.O.C. Wine Bar', 40.719581376893274, -73.96044547404588, '83 N 7th St (at Wythe Ave), Brooklyn, NY 11249, United States', 330, True, -5820968.89262285, 9863754.493601384)
('53014894498ee35b4045c7de', 'La Nonna Ristorante & Bar', 40.71857266955527, -73.96375090320407, '184 Kent Ave (btwn N 3rd & N 4th St), Brooklyn, NY 11249, United States', 284, True, -5821151.774432896, 9864176.347887658)
('4dcabca41f6e2812677e3598', 'The Meatball Shop', 40.71817031618937, -73.95750154418721, '170 Bedford Ave (btwn N 7th & N 8th St), Brooklyn, NY 11249, United States', 345, True, -5821197.706633946, 9863367.931338103)
('5040c59fe4b06a6d9df144c0', 'Antica Pesa', 40.7188427317835, -73.95866291941658, '115 Berry St, Bro

In [78]:
print('Restaurants around location')
print('---------------------------')
for i in range(100, 110):
    rs = location_restaurants[i][:8]
    names = ', '.join([r[1] for r in rs])
    print('Restaurants around location {}: {}'.format(i+1, names))


Restaurants around location
---------------------------
Restaurants around location 101: Iron Chef House, Sushi Gallery, Clark's Restaurant, Heights Falafel, Chipotle Mexican Grill, Kogane, Park Plaza Restaurant, Ozu Japanese Cuisine & Lounge
Restaurants around location 102: Henry's End, Westville DUMBO, Noodle Pudding, Heights Falafel, Jack the Horse Tavern, Tutt Cafe
Restaurants around location 103: Westville DUMBO, Atrium DUMBO, Rice & Miso Everyday, Cecconi's, Celestine, Gran Eléctrica, Bessou, Landhaus Under the Manhattan Bridge
Restaurants around location 104: Lucky Rice Night Market
Restaurants around location 105: Forever Taste, El Castillo de Madison Restaurant
Restaurants around location 106: Kiki's, Forgtmenot, l'estudio, Kopitiam, Cervo's, Les Enfants de Bohème, Eastwood, JaJaJa Plantas Mexicana
Restaurants around location 107: Simple, Orchard Grocer, Empanada Mama, Cafe Katja, Dudley's, Vanessa's Dumpling House, Ramen Ishida, l'estudio
Restaurants around location 108: Le F

Let's now see all the collected restaurants in our area of interest on map, and let's also show Italian restaurants in different color.

In [79]:
map_new_york_city = folium.Map(location=new_york_city_center, zoom_start=13)
folium.Marker(new_york_city_center, popup='New York City').add_to(map_new_york_city)
for res in restaurants.values():
    lat = res[2]; lon = res[3]
    is_italian = res[6]
    color = 'red' if is_italian else 'blue'
    folium.CircleMarker([lat, lon], radius=3, color=color, fill=True, fill_color=color, fill_opacity=1).add_to(map_new_york_city)
map_new_york_city

Looking good. So now we have all the restaurants in area within few kilometers from city center, and we know which ones are Italian restaurants! We also know which restaurants exactly are in vicinity of every neighborhood candidate center.

This concludes the data gathering phase - we're now ready to use this data for analysis to produce the report on optimal locations for a new Italian restaurant!

## Methodology <a name="methodology"></a>

In this project we will direct our efforts on detecting areas of New York City that have low restaurant density, particularly those with low number of Italian restaurants. We will limit our analysis to area ~6km around city center.

In first step we have collected the required **data: location and type (category) of every restaurant within 6km from city center**. We have also **identified Italian restaurants** (according to Foursquare categorization).

Second step in our analysis will be calculation and exploration of '**restaurant density**' across different areas of New York city - we will use **heatmaps** to identify a few promising areas close to center with low number of restaurants in general (*and* no Italian restaurants in vicinity) and focus our attention on those areas.

In third and final step we will focus on most promising areas and within those create **clusters of locations that meet some basic requirements** established in discussion with stakeholders: we will take into consideration locations with **no more than two restaurants in radius of 250 meters**, and we want locations **without Italian restaurants in radius of 400 meters**. We will present map of all such locations but also create clusters (using **k-means clustering**) of those locations to identify general zones / neighborhoods / addresses which should be a starting point for final 'street level' exploration and search for optimal venue location by stakeholders.

## Analysis <a name="analysis"></a>

Let's perform some basic explanatory data analysis and derive some additional info from our raw data. First let's count the **number of restaurants in every area candidate**:

In [80]:
location_restaurants_count = [len(res) for res in location_restaurants]

df_locations['Restaurants in area'] = location_restaurants_count

print('Average number of restaurants in every area with radius=300m:', np.array(location_restaurants_count).mean())

df_locations.head(10)

Average number of restaurants in every area with radius=300m: 9.10989010989011


Address   Latitude  Longitude             X  \
0   1626 Hooper St, Brooklyn, NY 11211  40.701263 -73.962112 -5.824082e+06   
1  556 Bedford Ave, Brooklyn, NY 11249  40.704797 -73.961984 -5.823482e+06   
2     172 S 9th St, Brooklyn, NY 11211  40.708330 -73.961856 -5.822882e+06   
3     158 S 3rd St, Brooklyn, NY 11211  40.711864 -73.961727 -5.822282e+06   
4     129 N 1st St, Brooklyn, NY 11249  40.715399 -73.961599 -5.821682e+06   
5      76 N 6th St, Brooklyn, NY 11249  40.718933 -73.961470 -5.821082e+06   
6    10 Nassau Ave, Brooklyn, NY 11222  40.722468 -73.961342 -5.820482e+06   
7     299 Park Ave, Brooklyn, NY 10017  40.696048 -73.966325 -5.824982e+06   
8  22 Flushing Ave, Brooklyn, NY 11205  40.699581 -73.966197 -5.824382e+06   
9     595 Kent Ave, Brooklyn, NY 11249  40.703114 -73.966069 -5.823782e+06   

              Y  Distance from center  Restaurants in area  
0  9.863884e+06           5992.495307                    1  
1  9.863884e+06           5840.376700                    1  
2  9.863884e+06           5747.173218                    5  
3  9.863884e+06           5715.767665                   31  
4  9.863884e+06           5747.173218                   35  
5  9.863884e+06           5840.376700                   17  
6  9.863884e+06           5992.495307                    6  
7  9.864403e+06           5855.766389                    8  
8  9.864403e+06           5604.462508                    0  
9  9.864403e+06           5408.326913                    1

OK, now let's calculate the **distance to nearest Italian restaurant from every area candidate center** (not only those within 300m - we want distance to closest one, regardless of how distant it is).

In [81]:
distances_to_italian_restaurant = []

for area_x, area_y in zip(xs, ys):
    min_distance = 10000
    for res in italian_restaurants.values():
        res_x = res[7]
        res_y = res[8]
        d = calc_xy_distance(area_x, area_y, res_x, res_y)
        if d<min_distance:
            min_distance = d
    distances_to_italian_restaurant.append(min_distance)

df_locations['Distance to Italian restaurant'] = distances_to_italian_restaurant

In [82]:
df_locations.head(200)

Address   Latitude  Longitude  \
0                   1626 Hooper St, Brooklyn, NY 11211  40.701263 -73.962112   
1                  556 Bedford Ave, Brooklyn, NY 11249  40.704797 -73.961984   
2                     172 S 9th St, Brooklyn, NY 11211  40.708330 -73.961856   
3                     158 S 3rd St, Brooklyn, NY 11211  40.711864 -73.961727   
4                     129 N 1st St, Brooklyn, NY 11249  40.715399 -73.961599   
5                      76 N 6th St, Brooklyn, NY 11249  40.718933 -73.961470   
6                    10 Nassau Ave, Brooklyn, NY 11222  40.722468 -73.961342   
7                     299 Park Ave, Brooklyn, NY 10017  40.696048 -73.966325   
8                  22 Flushing Ave, Brooklyn, NY 11205  40.699581 -73.966197   
9                     595 Kent Ave, Brooklyn, NY 11249  40.703114 -73.966069   
10                 64 Division Ave, Brooklyn, NY 11249  40.706648 -73.965941   
11                     84 Broadway, Brooklyn, NY 11249  40.710182 -73.965813   
12                     51 S 3rd St, Brooklyn, NY 11249  40.713716 -73.965686   
13                     33 N 1st St, Brooklyn, NY 11249  40.717250 -73.965558   
14   East River Memorial Bench, North, Brooklyn, NY...  40.720785 -73.965430   
15                    108 Kent Ave, Brooklyn, NY 11249  40.724320 -73.965302   
16                                  New York, NY 10009  40.727855 -73.965174   
17                223 Clermont Ave, Brooklyn, NY 11205  40.690833 -73.970536   
18              110 Vanderbilt Ave, Brooklyn, NY 11205  40.694365 -73.970408   
19                154 Flushing Ave, Brooklyn, NY 11205  40.697898 -73.970281   
20   Building 293, Brooklyn Navy Yard, Gee Ave, Bro...  40.701432 -73.970154   
21          Railroad Ave & Kay Ave, Brooklyn, NY 11249  40.704965 -73.970026   
22   South Williamsburg, 440 Kent Ave, Brooklyn, NY...  40.708499 -73.969899   
23                    380 Kent Ave, Brooklyn, NY 11249  40.712033 -73.969772   
24                     25 River St, Brooklyn, NY 11249  40.715567 -73.969644   
25                     ST1 West St, Brooklyn, NY 11222  40.719102 -73.969517   
26   East River Park Field 8, East River Park, East...  40.722637 -73.969389   
27                     1119 FDR Dr, New York, NY 10009  40.726172 -73.969262   
28                FDR Dr N/E 20 St, New York, NY 10009  40.729707 -73.969135   
29                                  Brooklyn, NY 11222  40.733242 -73.969007   
..                                                 ...        ...        ...   
170                  269 W 16th St, New York, NY 10011  40.740976 -74.000962   
171                  329 W 21st St, New York, NY 10011  40.744512 -74.000839   
172                  26 Delavan St, Brooklyn, NY 11231  40.679211 -74.007140   
173               128 Van Brunt St, Brooklyn, NY 11231  40.682743 -74.007017   
174                   8 Sackett St, Brooklyn, NY 11231  40.686275 -74.006894   
175                 70 Columbia St, Brooklyn, NY 11201  40.689808 -74.006771   
176  Brooklyn Bridge Park Pier 6 / Atlantic Avenue,...  40.693341 -74.006649   
177                            Manhattan, New York, NY  40.696874 -74.006526   
178  Heliport, Downtown Manhattan Heliport, 6 East ...  40.700407 -74.006403   
179                    223 Wall St, New York, NY 10005  40.703940 -74.006280   
180                     4 Platt St, New York, NY 10038  40.707474 -74.006157   
181  Entrance on Beekman, 8 Spruce St, New York, NY...  40.711008 -74.006034   
182                   280 Broadway, New York, NY 10007  40.714542 -74.005911   
183                  250 Church St, New York, NY 10013  40.718077 -74.005788   
184           Canal Street Station, New York, NY 10013  40.721612 -74.005665   
185                  246 Spring St, New York, NY 10013  40.725147 -74.005542   
186                  207 Varick St, New York, NY 10014  40.728682 -74.005419   
187                  90 Bedford St, New York, NY 10014  40.732217 -74.005296   
188                400 Bleecker St, New York, N

In [83]:
print('Average distance to closest Italian restaurant from each area center:', df_locations['Distance to Italian restaurant'].mean())

Average distance to closest Italian restaurant from each area center: 825.6983452818165


OK, so **on average Italian restaurant can be found within ~500m** from every area center candidate. That's fairly close, so we need to filter our areas carefully!

Let's crete a map showing heatmap / density of restaurants and try to extract some meaningfull info from that. Also, let's show borders of New York boroughs on our map and a few circles indicating distance of 1km, 2km and 3km from city center.



In [84]:
# new_york_city_boroughs_url = 'https://geo.nyu.edu/catalog/nyu_2451_34572'
# new_york_city_boroughs = requests.get(new_york_city_boroughs_url).json()

# def boroughs_style(feature):
#    return { 'color': 'blue', 'fill': False }

In [85]:
import json # library to handle JSON files

!wget -q -O 'newyork_data.json' https://cocl.us/new_york_dataset
print('Data downloaded!')

Data downloaded!


In [86]:
with open('newyork_data.json') as json_data:
    new_york_city_boroughs = json.load(json_data)

In [87]:
def boroughs_style(feature):
    return { 'color': 'blue', 'fill': False }

In [88]:
restaurant_latlons = [[res[2], res[3]] for res in restaurants.values()]

italian_latlons = [[res[2], res[3]] for res in italian_restaurants.values()]

In [89]:
from folium import plugins
from folium.plugins import HeatMap

map_new_york_city = folium.Map(location=new_york_city_center, zoom_start=13)
folium.TileLayer('cartodbpositron').add_to(map_new_york_city) #cartodbpositron cartodbdark_matter
HeatMap(restaurant_latlons).add_to(map_new_york_city)
folium.Marker(new_york_city_center).add_to(map_new_york_city)
folium.Circle(new_york_city_center, radius=1000, fill=False, color='white').add_to(map_new_york_city)
folium.Circle(new_york_city_center, radius=2000, fill=False, color='white').add_to(map_new_york_city)
folium.Circle(new_york_city_center, radius=3000, fill=False, color='white').add_to(map_new_york_city)
folium.GeoJson(new_york_city_boroughs, style_function=boroughs_style, name='geojson').add_to(map_new_york_city)
map_new_york_city

Looks like a few pockets of low restaurant density closest to city center can be found **south, south-east and east from city center**. 

Let's create another heatmap map showing **heatmap/density of Italian restaurants** only.

In [90]:
map_new_york_city = folium.Map(location=new_york_city_center, zoom_start=13)
folium.TileLayer('cartodbpositron').add_to(map_new_york_city) #cartodbpositron cartodbdark_matter
HeatMap(italian_latlons).add_to(map_new_york_city)
folium.Marker(new_york_city_center).add_to(map_new_york_city)
folium.Circle(new_york_city_center, radius=1000, fill=False, color='white').add_to(map_new_york_city)
folium.Circle(new_york_city_center, radius=2000, fill=False, color='white').add_to(map_new_york_city)
folium.Circle(new_york_city_center, radius=3000, fill=False, color='white').add_to(map_new_york_city)
folium.GeoJson(new_york_city_boroughs, style_function=boroughs_style, name='geojson').add_to(map_new_york_city)
map_new_york_city


This map is not so 'hot' (Italian restaurants represent a subset of ~15% of all restaurants in New York City) but it also indicates higher density of existing Italian restaurants directly north and west from New York, with closest pockets of **low Italian restaurant density positioned south, north-west from city center**.

Based on this we will now focus our analysis on areas *south-west, south, south-east and east from New York City center* - we will move the center of our area of interest and reduce it's size to have a radius of **2.5km**. This places our location candidates mostly in boroughs **South Street(Manhattan) and Brooklyn Street Circuit**.

### South Street(Manhattan) and Brooklyn Street Circuit

Analysis of popular travel guides and web sites often mention South Street(Manhattan) and Brooklyn Street Circuit as beautifull, interesting, rich with culture,  technological innovations and electric- and hybrid-powered production vehicles, racing simulators and 'cool' New York City neighborhoods popular with tourists.

*The South street has often been used as a location for Hollywood movies, including A Hatful of Rain, which was filmed in 1957 at Knickerbocker Village. South Street was the setting for the 1953 Sam Fuller film Pickup on South Street.."* (wikipedia.org)

Popular with tourists, alternative and bohemian but booming and trendy, relatively close to city center and well connected, those boroughs appear to justify further analysis.

Let's define new, more narrow region of interest, which will include low-restaurant-count parts of South Street(Manhattan) and Brooklyn Street Circuit closest to Ney York City.

In [91]:
roi_x_min = new_york_city_center_x - 2000
roi_y_max = new_york_city_center_y + 1000
roi_width = 5000
roi_height = 5000
roi_center_x = roi_x_min + 2500
roi_center_y = roi_y_max - 2500
roi_center_lon, roi_center_lat = xy_to_lonlat(roi_center_x, roi_center_y)
roi_center = [roi_center_lat, roi_center_lon]

map_new_york_city = folium.Map(location=roi_center, zoom_start=14)
HeatMap(restaurant_latlons).add_to(map_new_york_city)
folium.Marker(new_york_city_center).add_to(map_new_york_city)
folium.Circle(roi_center, radius=2500, color='white', fill=True, fill_opacity=0.4).add_to(map_new_york_city)
folium.GeoJson(new_york_city_boroughs, style_function=boroughs_style, name='geojson').add_to(map_new_york_city)
map_new_york_city

/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1


This nicely covers all the pockets of low restaurant density in Kreuzberg and Friedrichshain closest to Berlin center.

Let's also create new, more dense grid of location candidates restricted to our new region of interest (let's make our location candidates 100m appart).

In [92]:
k = math.sqrt(3) / 2 # Vertical offset for hexagonal grid cells
x_step = 100
y_step = 100 * k 
roi_y_min = roi_center_y - 2500

roi_latitudes = []
roi_longitudes = []
roi_xs = []
roi_ys = []
for i in range(0, int(51/k)):
    y = roi_y_min + i * y_step
    x_offset = 50 if i%2==0 else 0
    for j in range(0, 51):
        x = roi_x_min + j * x_step + x_offset
        d = calc_xy_distance(roi_center_x, roi_center_y, x, y)
        if (d <= 2501):
            lon, lat = xy_to_lonlat(x, y)
            roi_latitudes.append(lat)
            roi_longitudes.append(lon)
            roi_xs.append(x)
            roi_ys.append(y)

print(len(roi_latitudes), 'candidate neighborhood centers generated.')

/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:18: DeprecationWarning: This function

/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:18: DeprecationWarning: This function

/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:18: DeprecationWarning: This function

/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:18: DeprecationWarning: This function

/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:18: DeprecationWarning: This function

...

/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:18: DeprecationWarning: This function

/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:18: DeprecationWarning: This function

/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:18: DeprecationWarning: This function

2261 candidate neighborhood centers generated.


/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1


OK. Now let's calculate two most important things for each location candidate: **number of restaurants in vicinity** (we'll use radius of **250 meters**) and **distance to closest Italian restaurant**.

In [93]:
def count_restaurants_nearby(x, y, restaurants, radius=250):    
    count = 0
    for res in restaurants.values():
        res_x = res[7]; res_y = res[8]
        d = calc_xy_distance(x, y, res_x, res_y)
        if d<=radius:
            count += 1
    return count

def find_nearest_restaurant(x, y, restaurants):
    d_min = 100000
    for res in restaurants.values():
        res_x = res[7]; res_y = res[8]
        d = calc_xy_distance(x, y, res_x, res_y)
        if d<=d_min:
            d_min = d
    return d_min

roi_restaurant_counts = []
roi_italian_distances = []

print('Generating data on location candidates... ', end='')
for x, y in zip(roi_xs, roi_ys):
    count = count_restaurants_nearby(x, y, restaurants, radius=250)
    roi_restaurant_counts.append(count)
    distance = find_nearest_restaurant(x, y, italian_restaurants)
    roi_italian_distances.append(distance)
print('done.')


Generating data on location candidates... done.


In [94]:
# Let's put this into dataframe
df_roi_locations = pd.DataFrame({'Latitude':roi_latitudes,
                                 'Longitude':roi_longitudes,
                                 'X':roi_xs,
                                 'Y':roi_ys,
                                 'Restaurants nearby':roi_restaurant_counts,
                                 'Distance to Italian restaurant':roi_italian_distances})

df_roi_locations.head(10)

Latitude  Longitude             X             Y  Restaurants nearby  \
0  40.714793 -73.974914 -5.821832e+06  9.865599e+06                   1   
1  40.715382 -73.974893 -5.821732e+06  9.865599e+06                   0   
2  40.711567 -73.975700 -5.822382e+06  9.865686e+06                   0   
3  40.712156 -73.975679 -5.822282e+06  9.865686e+06                   0   
4  40.712745 -73.975658 -5.822182e+06  9.865686e+06                   1   
5  40.713334 -73.975637 -5.822082e+06  9.865686e+06                   1   
6  40.713923 -73.975616 -5.821982e+06  9.865686e+06                   1   
7  40.714512 -73.975595 -5.821882e+06  9.865686e+06                   1   
8  40.715101 -73.975574 -5.821782e+06  9.865686e+06                   1   
9  40.715690 -73.975552 -5.821682e+06  9.865686e+06                   0   

   Distance to Italian restaurant  
0                      986.331907  
1                     1029.602465  
2                      819.723822  
3                      840.138322  
4                      871.617839  
5                      913.018572  
6                      963.061872  
7                     1020.477058  
8                     1084.093484  
9                     1127.183526

OK. Let us now **filter** those locations: we're interested only in **locations with no more than two restaurants in radius of 250 meters**, and **no Italian restaurants in radius of 400 meters**

In [95]:
good_res_count = np.array((df_roi_locations['Restaurants nearby']<=2))
print('Locations with no more than two restaurants nearby:', good_res_count.sum())

good_ita_distance = np.array(df_roi_locations['Distance to Italian restaurant']>=400)
print('Locations with no Italian restaurants within 400m:', good_ita_distance.sum())

good_locations = np.logical_and(good_res_count, good_ita_distance)
print('Locations with both conditions met:', good_locations.sum())

df_good_locations = df_roi_locations[good_locations]

Locations with no more than two restaurants nearby: 876
Locations with no Italian restaurants within 400m: 977
Locations with both conditions met: 706


Let's see how this looks on a map.

In [96]:
good_latitudes = df_good_locations['Latitude'].values
good_longitudes = df_good_locations['Longitude'].values

good_locations = [[lat, lon] for lat, lon in zip(good_latitudes, good_longitudes)]

map_new_york_city = folium.Map(location=roi_center, zoom_start=14)
folium.TileLayer('cartodbpositron').add_to(map_new_york_city)
HeatMap(restaurant_latlons).add_to(map_new_york_city)
folium.Circle(roi_center, radius=2500, color='white', fill=True, fill_opacity=0.6).add_to(map_new_york_city)
folium.Marker(new_york_city_center).add_to(map_new_york_city)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_new_york_city) 
folium.GeoJson(new_york_city_boroughs, style_function=boroughs_style, name='geojson').add_to(map_new_york_city)
map_new_york_city

Looking good. We now have a bunch of locations fairly close New York City, and we know that each of those locations has no more than two restaurants in radius of 250m, and no Italian restaurant closer than 400m. Any of those locations is a potential candidate for a new Italian restaurant, at least based on nearby competition.

Let's now show those good locations in a form of heatmap:

In [97]:
map_new_york_city = folium.Map(location=roi_center, zoom_start=14)
HeatMap(good_locations, radius=25).add_to(map_new_york_city)
folium.Marker(new_york_city_center).add_to(map_new_york_city)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_new_york_city)
folium.GeoJson(new_york_city_boroughs, style_function=boroughs_style, name='geojson').add_to(map_new_york_city)
map_new_york_city

Looking good. What we have now is a clear indication of zones with low number of restaurants in vicinity, and *no* Italian restaurants at all nearby.

Let us now **cluster** those locations to create **centers of zones containing good locations**. Those zones, their centers and addresses will be the final result of our analysis. 

In [98]:
from sklearn.cluster import KMeans

number_of_clusters = 15

good_xys = df_good_locations[['X', 'Y']].values
kmeans = KMeans(n_clusters=number_of_clusters, random_state=0).fit(good_xys)

cluster_centers = [xy_to_lonlat(cc[0], cc[1]) for cc in kmeans.cluster_centers_]

map_new_york_city = folium.Map(location=roi_center, zoom_start=14)
folium.TileLayer('cartodbpositron').add_to(map_new_york_city)
HeatMap(restaurant_latlons).add_to(map_new_york_city)
folium.Circle(roi_center, radius=2500, color='white', fill=True, fill_opacity=0.4).add_to(map_new_york_city)
folium.Marker(new_york_city_center).add_to(map_new_york_city)
for lon, lat in cluster_centers:
    folium.Circle([lat, lon], radius=500, color='green', fill=True, fill_opacity=0.25).add_to(map_new_york_city) 
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_new_york_city)
folium.GeoJson(new_york_city_boroughs, style_function=boroughs_style, name='geojson').add_to(map_new_york_city)
map_new_york_city

/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:18: DeprecationWarning: This function

Not bad - our clusters represent groupings of most of the candidate locations and cluster centers are placed nicely in the middle of the zones 'rich' with location candidates.

Addresses of those cluster centers will be a good starting point for exploring the neighborhoods to find the best possible location based on neighborhood specifics.

Let's see those zones on a city map without heatmap, using shaded areas to indicate our clusters:

In [99]:
map_new_york_city = folium.Map(location=roi_center, zoom_start=14)
folium.Marker(new_york_city_center).add_to(map_new_york_city)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.Circle([lat, lon], radius=250, color='#00000000', fill=True, fill_color='#0066ff', fill_opacity=0.07).add_to(map_new_york_city)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_new_york_city)
for lon, lat in cluster_centers:
    folium.Circle([lat, lon], radius=500, color='green', fill=False).add_to(map_new_york_city) 
folium.GeoJson(new_york_city_boroughs, style_function=boroughs_style, name='geojson').add_to(map_new_york_city)
map_new_york_city

Let's zoom in on candidate areas in **South Street(Manhattan)**:

In [100]:
map_new_york_city = folium.Map(location=[52.498972, 13.409591], zoom_start=15)
folium.Marker(new_york_city_center).add_to(map_new_york_city)
for lon, lat in cluster_centers:
    folium.Circle([lat, lon], radius=500, color='green', fill=False).add_to(map_new_york_city) 
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.Circle([lat, lon], radius=250, color='#0000ff00', fill=True, fill_color='#0066ff', fill_opacity=0.07).add_to(map_new_york_city)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_new_york_city)
folium.GeoJson(new_york_city_boroughs, style_function=boroughs_style, name='geojson').add_to(map_new_york_city)
map_new_york_city

...and candidate areas in *Brooklyn Street Circuit**:

In [101]:
map_new_york_city = folium.Map(location=[52.516347, 13.428403], zoom_start=15)
folium.Marker(new_york_city_center).add_to(map_new_york_city)
for lon, lat in cluster_centers:
    folium.Circle([lat, lon], radius=500, color='green', fill=False).add_to(map_new_york_city) 
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.Circle([lat, lon], radius=250, color='#0000ff00', fill=True, fill_color='#0066ff', fill_opacity=0.07).add_to(map_new_york_city)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_new_york_city)
folium.GeoJson(new_york_city_boroughs, style_function=boroughs_style, name='geojson').add_to(map_new_york_city)
map_new_york_city

Finaly, let's **reverse geocode those candidate area centers to get the addresses** which can be presented to stakeholders.

In [102]:
candidate_area_addresses = []
print('==============================================================')
print('Addresses of centers of areas recommended for further analysis')
print('==============================================================\n')
for lon, lat in cluster_centers:
    addr = get_address(google_api_key, lat, lon).replace(', USA', '')
    candidate_area_addresses.append(addr)    
    x, y = lonlat_to_xy(lon, lat)
    d = calc_xy_distance(x, y, new_york_city_center_x, new_york_city_center_y)
    print('{}{} => {:.1f}km from new york city'.format(addr, ' '*(50-len(addr)), d/1000))

Addresses of centers of areas recommended for further analysis



/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:12: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1


Brooklyn Bridge Promenade, New York, NY 10038      => 1.7km from new york city


/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:12: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1


44 South St, New York, NY 10005                    => 3.4km from new york city


...

/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:12: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1


621 Water St, New York, NY 10002                   => 2.9km from new york city


/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:12: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1


Unnamed Road, Brooklyn, NY 11201                   => 1.9km from new york city
1201 Cherry St, New York, NY 10002                 => 3.6km from new york city


/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:12: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1


This concludes our analysis. We have created 15 addresses representing centers of zones containing locations with low number of restaurants and no Italian restaurants nearby, all zones being fairly close to city center (all less than 4km from Alexanderplazt, and about half of those less than 2km from Alexanderplatz). Although zones are shown on map with a radius of ~500 meters (green circles), their shape is actually very irregular and their centers/addresses should be considered only as a starting point for exploring area neighborhoods in search for potential restaurant locations. Most of the zones are located in Kreuzberg and Friedrichshain boroughs, which we have identified as interesting due to being popular with tourists, fairly close to city center and well connected by public transport.

In [103]:
map_new_york_city = folium.Map(location=roi_center, zoom_start=14)
folium.Circle(new_york_city_center, radius=50, color='red', fill=True, fill_color='red', fill_opacity=1).add_to(map_new_york_city)
for lonlat, addr in zip(cluster_centers, candidate_area_addresses):
    folium.Marker([lonlat[1], lonlat[0]], popup=addr).add_to(map_new_york_city) 
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.Circle([lat, lon], radius=250, color='#0000ff00', fill=True, fill_color='#0066ff', fill_opacity=0.05).add_to(map_new_york_city)
map_new_york_city

## Results and Discussion

The analysis showed that although there was a great number of restaurants in New York City, there were packets of low restaurant density fairly close to city center. Highest concentration of restaurants was detected south and north-west from New York City, so I focused my attention to areas south of South Street( Manhattan) and north-west of Brooklyn Street circuit. 
I firstly created a dense grid of location candidates (spaced 100m appart) those locations were then filtered so that those with more than two restaurants in radius of 250m and those with an Italian restaurant closer than 400m were removed.
Those location candidates were then clustered to create zones of interest which contain greatest number of location candidates. Addresses of centers of those zones were also generated using reverse geocoding to be used as markers/starting points for more detailed local analysis based on other factors.
Result of all this is 15 zones containing largest number of potential new restaurant locations based on number of and distance to existing venues - both restaurants in general and Italian restaurants particularly. This, of course, does not imply that those zones are actually optimal locations for a new restaurant! Purpose of this analysis was to only provide info on areas close to Berlin center but not crowded with existing restaurants (particularly Italian) - it is entirely possible that there is a very good reason for small number of restaurants in any of those areas, reasons which would make them unsuitable for a new restaurant regardless of lack of competition in the area. Recommended zones should therefore be considered only as a starting point for more detailed analysis which could eventually result in location which has not only no nearby competition but also other factors taken into account and all other relevant conditions met.


## Conclusion

The purpose of this project was to identify New York City areas close to center with low number of restaurants and particularly the Italian restaurants in order to aid stakeholders in narrowing down the search for optimal location for a new Italian restaurant. By calculating restaurant density distribution from Foursquare data we have first identified general boroughs that justify further analysis (South Street( Manhattan) and Brooklyn Street circuit) and then generated extensive collection of locations which satisfy some basic requirements regarding existing nearby restaurants. Clustering of those locations was then performed in order to create major zones of interest which contained greatest number of potential location and addresses of those zone centers were created to be used as starting points for final exploration by stakeholders.
Final decision on optimal restaurant location will be made by stakeholders based on specific characteristics of neighborhoods and locations in every recommended zone, taking into consideration additional factors like attractiveness of each location, levels of noise / proximity to major roads, real estate availability, prices, social and economic dynamics of every neighborhood etc.
